<a href="https://www.kaggle.com/ranjeetshrivastav/tps-feb-22-lightgbm?scriptVersionId=88443200" target="_blank"><img align="left" alt="Kaggle" title="Open in Kaggle" src="https://kaggle.com/static/images/open-in-kaggle.svg"></a>

In [1]:
import numpy as np 
import pandas as pd
import matplotlib.pyplot as plt
%matplotlib inline
import seaborn as sns
import plotly.graph_objects as go
import warnings
warnings.filterwarnings('ignore')

from sklearn.model_selection import KFold, train_test_split
from lightgbm import LGBMClassifier
from sklearn.metrics import accuracy_score

In [2]:
train = pd.read_csv(r'../input/tabular-playground-series-feb-2022/train.csv')
train.head()

row_id     A0T0G0C10  A0T0G1C9  A0T0G2C8  A0T0G3C7  A0T0G4C6  A0T0G5C5  \
0       0 -9.536743e-07 -0.000010 -0.000043 -0.000114 -0.000200 -0.000240   
1       1 -9.536743e-07 -0.000010 -0.000043  0.000886 -0.000200  0.000760   
2       2 -9.536743e-07 -0.000002  0.000007  0.000129  0.000268  0.000270   
3       3  4.632568e-08 -0.000006  0.000012  0.000245  0.000492  0.000522   
4       4 -9.536743e-07 -0.000010 -0.000043 -0.000114 -0.000200 -0.000240   

   A0T0G6C4  A0T0G7C3  A0T0G8C2  ...  A8T0G1C1  A8T0G2C0  A8T1G0C1  A8T1G1C0  \
0 -0.000200 -0.000114 -0.000043  ... -0.000086 -0.000043 -0.000086 -0.000086   
1 -0.000200 -0.000114 -0.000043  ... -0.000086 -0.000043  0.000914  0.000914   
2  0.000243  0.000125  0.000001  ...  0.000084  0.000048  0.000081  0.000106   
3  0.000396  0.000197 -0.000003  ...  0.000151  0.000100  0.000180  0.000202   
4 -0.000200 -0.000114 -0.000043  ... -0.000086 -0.000043 -0.000086 -0.000086   

   A8T2G0C0  A9T0G0C1  A9T0G1C0  A9T1G0C0     A10T0G0C0  \
0 -0.000043 -0.000010 -0.000010 -0.000010 -9.536743e-07   
1 -0.000043 -0.000010 -0.000010 -0.000010 -9.536743e-07   
2  0.000072  0.000010  0.000008  0.000019  1.046326e-06   
3  0.000153  0.000021  0.000015  0.000046 -9.536743e-07   
4 -0.000043 -0.000010 -0.000010 -0.000010 -9.536743e-07   

                   target  
0  Streptococcus_pyogenes  
1     Salmonella_enterica  
2     Salmonella_enterica  
3     Salmonella_enterica  
4      Enterococcus_hirae  

[5 rows x 288 columns]

In [3]:
test = pd.read_csv(r'../input/tabular-playground-series-feb-2022/test.csv')
test.head()

row_id     A0T0G0C10  A0T0G1C9      A0T0G2C8  A0T0G3C7  A0T0G4C6  A0T0G5C5  \
0  200000 -9.536743e-07 -0.000002 -9.153442e-07  0.000024  0.000034 -0.000002   
1  200001 -9.536743e-07 -0.000010 -4.291534e-05 -0.000114  0.001800 -0.000240   
2  200002  4.632568e-08  0.000003  8.465576e-08 -0.000014  0.000007 -0.000005   
3  200003 -9.536743e-07 -0.000008  8.084656e-06  0.000216  0.000420  0.000514   
4  200004 -9.536743e-07 -0.000010 -4.291534e-05 -0.000114 -0.000200 -0.000240   

   A0T0G6C4  A0T0G7C3  A0T0G8C2  ...  A8T0G0C2  A8T0G1C1  A8T0G2C0  A8T1G0C1  \
0  0.000021  0.000024 -0.000009  ...  0.000039  0.000085  0.000055  0.000108   
1  0.001800 -0.000114  0.000957  ... -0.000043  0.000914 -0.000043 -0.000086   
2 -0.000004  0.000003  0.000004  ...  0.000041  0.000102  0.000084  0.000111   
3  0.000452  0.000187 -0.000005  ...  0.000069  0.000158  0.000098  0.000175   
4 -0.000200 -0.000114 -0.000043  ... -0.000043 -0.000086 -0.000043 -0.000086   

   A8T1G1C0  A8T2G0C0  A9T0G0C1  A9T0G1C0  A9T1G0C0     A10T0G0C0  
0  0.000090  0.000059  0.000010  0.000006  0.000027  4.632568e-08  
1 -0.000086 -0.000043 -0.000010 -0.000010 -0.000010 -9.536743e-07  
2  0.000117  0.000070  0.000020  0.000030  0.000021  4.632568e-08  
3  0.000217  0.000150  0.000018  0.000016  0.000051 -9.536743e-07  
4  0.000914 -0.000043 -0.000010 -0.000010  0.000990 -9.536743e-07  

[5 rows x 287 columns]

In [4]:
sub = pd.read_csv(r'../input/tabular-playground-series-feb-2022/sample_submission.csv')
sub.head()

row_id                    target
0  200000  Streptococcus_pneumoniae
1  200001  Streptococcus_pneumoniae
2  200002  Streptococcus_pneumoniae
3  200003  Streptococcus_pneumoniae
4  200004  Streptococcus_pneumoniae

In [5]:
train.drop('row_id',axis=1,inplace=True)
test.drop('row_id',axis=1,inplace=True)

In [6]:
print(f'train set have {train.shape[0]} rows and {train.shape[1]} columns.')
print(f'test set have {test.shape[0]} rows and {test.shape[1]} columns.') 
print(f'sample_submission set have {sub.shape[0]} rows and {sub.shape[1]} columns.') 

train set have 200000 rows and 287 columns.
test set have 100000 rows and 286 columns.
sample_submission set have 100000 rows and 2 columns.


In [7]:
fig = go.Figure(data=[go.Pie(labels=train['target'], hole=.3)])
fig.add_annotation(text='Target',
                   x=0.5,y=0.5,showarrow=False,font_size=14,opacity=0.7,font_family='monospace')
fig.update_traces(hoverinfo='label+percent+value',
                  marker=dict(line=dict(color='#000000', width=2)))
fig.update_layout(
    font_family='monospace',
    title=dict(text='Target Unique Values',x=0.47,y=0.98,
               font=dict(color='black',size=20)),
    legend=dict(orientation='v',traceorder='reversed'),
    hoverlabel=dict(bgcolor='white'))
fig.update_traces(textposition='outside', textinfo='percent+label')
fig.show()

In [8]:
from sklearn.preprocessing import LabelEncoder
le = LabelEncoder()
train['target'] = le.fit_transform(train['target'])

In [9]:
y = train['target']
train.drop('target',axis=1,inplace=True)

In [10]:
features = []
for feature in train.columns:
    features.append(feature)
print(features)

['A0T0G0C10', 'A0T0G1C9', 'A0T0G2C8', 'A0T0G3C7', 'A0T0G4C6', 'A0T0G5C5', 'A0T0G6C4', 'A0T0G7C3', 'A0T0G8C2', 'A0T0G9C1', 'A0T0G10C0', 'A0T1G0C9', 'A0T1G1C8', 'A0T1G2C7', 'A0T1G3C6', 'A0T1G4C5', 'A0T1G5C4', 'A0T1G6C3', 'A0T1G7C2', 'A0T1G8C1', 'A0T1G9C0', 'A0T2G0C8', 'A0T2G1C7', 'A0T2G2C6', 'A0T2G3C5', 'A0T2G4C4', 'A0T2G5C3', 'A0T2G6C2', 'A0T2G7C1', 'A0T2G8C0', 'A0T3G0C7', 'A0T3G1C6', 'A0T3G2C5', 'A0T3G3C4', 'A0T3G4C3', 'A0T3G5C2', 'A0T3G6C1', 'A0T3G7C0', 'A0T4G0C6', 'A0T4G1C5', 'A0T4G2C4', 'A0T4G3C3', 'A0T4G4C2', 'A0T4G5C1', 'A0T4G6C0', 'A0T5G0C5', 'A0T5G1C4', 'A0T5G2C3', 'A0T5G3C2', 'A0T5G4C1', 'A0T5G5C0', 'A0T6G0C4', 'A0T6G1C3', 'A0T6G2C2', 'A0T6G3C1', 'A0T6G4C0', 'A0T7G0C3', 'A0T7G1C2', 'A0T7G2C1', 'A0T7G3C0', 'A0T8G0C2', 'A0T8G1C1', 'A0T8G2C0', 'A0T9G0C1', 'A0T9G1C0', 'A0T10G0C0', 'A1T0G0C9', 'A1T0G1C8', 'A1T0G2C7', 'A1T0G3C6', 'A1T0G4C5', 'A1T0G5C4', 'A1T0G6C3', 'A1T0G7C2', 'A1T0G8C1', 'A1T0G9C0', 'A1T1G0C8', 'A1T1G1C7', 'A1T1G2C6', 'A1T1G3C5', 'A1T1G4C4', 'A1T1G5C3', 'A1T1G6C2', 

In [11]:
from sklearn.preprocessing import StandardScaler
scale = StandardScaler()
train[features] = scale.fit_transform(train[features])
test[features] = scale.transform(test[features])

In [12]:
def fit_lgb(trial, x_train, y_train, x_test, y_test):
    params = {
        'reg_alpha' : trial.suggest_loguniform('reg_alpha' , 1e-4, 1e4),
        'reg_lambda' : trial.suggest_loguniform('reg_lambda' ,1e-4, 1e4),
        'learning_rate' : trial.suggest_uniform('learning_rate' , 0.03 , 0.07),
        'max_depth' : trial.suggest_int('max_depth', 1 , 20),
        'n_estimators' : trial.suggest_int('n_estimators', 100 , 20000),
        'min_child_weight' : trial.suggest_loguniform('min_child_weight', 1e-4, 1e4),
        'subsample' : trial.suggest_uniform('subsample' , 0.01 , 2.0),
        'min_child_samples' : trial.suggest_int('min_child_samples', 76, 80),
        'device_type' : 'gpu','n_jobs':4
    } 
    
    
    model = LGBMClassifier(**params)
    model.fit(x_train, y_train,eval_set=[(x_test,y_test)], early_stopping_rounds=150, verbose=False)
    
    y_train_pred = model.predict(x_train)
    y_train_pred = [round(value) for value in y_train_pred]
    
    y_test_pred = model.predict(x_test)
    y_test_pred = [round(value) for value in y_test_pred]
    
    
    log = {
        "train accuracy": accuracy_score(y_train, y_train_pred),
        "valid accuracy": accuracy_score(y_test, y_test_pred)
    }
    
    return model, log

In [13]:
def objective(trial):
    acc = 0
    x_train, x_test, y_train, y_test = train_test_split(train, y, test_size=0.30)
    model, log = fit_lgb(trial, x_train, y_train, x_test, y_test)
    acc += log['valid accuracy']
        
    return acc

In [14]:
params = {'reg_alpha': 0.0038667681867618933, 
 'reg_lambda': 0.636197588712714, 
 'learning_rate': 0.047206888009302006, 
 'max_depth': 11, 
 'n_estimators': 6786, 
 'min_child_samples': 79,'device_type' : 'gpu'}

In [15]:
folds = KFold(n_splits=5, shuffle=True)

lgb_predictions = np.zeros(len(test))

for fold, (trn_idx, val_idx) in enumerate(folds.split(train)):
    print(f"Fold: {fold}")
    X_train, X_test = train.iloc[trn_idx], train.iloc[val_idx]
    y_train, y_test = y.iloc[trn_idx], y.iloc[val_idx]

    model = LGBMClassifier(**params)
   
    model.fit(X_train, y_train,
              eval_set=[(X_test, y_test)],
                early_stopping_rounds=400,
                verbose=False)
    y_pred = model.predict(X_test)
    pred = [round(value) for value in y_pred]
    acc = accuracy_score(y_test, y_pred)
    
    print(f" accuracy: {acc*100}%")
    print("-"*50)

Fold: 0
 accuracy: 99.58500000000001%
--------------------------------------------------
Fold: 1
 accuracy: 99.595%
--------------------------------------------------
Fold: 2
 accuracy: 99.6125%
--------------------------------------------------
Fold: 3
 accuracy: 99.565%
--------------------------------------------------
Fold: 4
 accuracy: 99.555%
--------------------------------------------------


In [16]:
lgb_predictions = model.predict(test)

In [17]:
sub['target'] = le.inverse_transform(lgb_predictions)
sub.to_csv(f'lgb.csv',index = False)

### WORK IN PROGRESS....